In [1]:
import importlib, importlib.util, subprocess, sys, os

def pip_install(pkg, no_deps=True, quiet=True):
    cmd = [sys.executable, "-m", "pip", "install"]
    if quiet:
        cmd.append("--quiet")
    if no_deps:
        cmd.append("--no-deps")
    cmd.append(pkg)
    subprocess.check_call(cmd)

def ensure_pkg(pip_name, module_name=None, no_deps=True):
    module_name = module_name or pip_name.split("==")[0].replace("-", "_")
    if importlib.util.find_spec(module_name) is None:
        print(f"Installing {pip_name} ...")
        try:
            pip_install(pip_name, no_deps=no_deps)
        except Exception as e:
            print(f"Failed to install {pip_name}: {e}")
    else:
        print(f"{module_name} already installed, skipping.")

# On Kaggle / Colab environments we must NOT upgrade numpy/scipy/pyarrow/shapely etc.
# Only install optional packages if missing, and install them without pulling dependencies.
optional_packages = {
    "tqdm": "tqdm",
    "opencv-python": "cv2",
    "imagehash": "imagehash",
    #"ffmpeg-python": "ffmpeg",
    #"einops": "einops"
}

for pip_name, module_name in optional_packages.items():
    ensure_pkg(pip_name, module_name, no_deps=True)

# Install torch only if missing; prefer system-provided CUDA-enabled build on Kaggle.
if importlib.util.find_spec("torch") is None:
    # install minimal torch without deps; adapt version if needed for your environment
    ensure_pkg("torch", "torch", no_deps=True)
else:
    print("torch already present, skipping installation.")

tqdm already installed, skipping.
cv2 already installed, skipping.
imagehash already installed, skipping.
torch already present, skipping installation.


In [2]:
!pip install ffmpeg-python
!pip install einops

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.4/64.4 kB 2.4 MB/s eta 0:00:00


In [3]:
import torch.nn as nn
class Linear_(nn.Module):
    def __init__(self, in_features, out_features, bias=True, act="ReLU", is_folded=True):
        super(Linear_, self).__init__()
        self.in_features = in_features
        self.out_features = out_features
        self.bias = bias
        self.act_type = act
        self.is_folded = is_folded
        self.linear = nn.Linear(in_features=self.in_features,
                                out_features=self.out_features,
                                bias=self.bias)
        self.act = _act(self.act_type)

    def forward(self, inputs):
        result_linear = self.linear(inputs)
        result = self.act(result_linear)
        return result

    @property
    def multiply_adds(self):
        result = self.in_features * self.out_features
        return result

    @property
    def params(self):
        params = self.in_features * self.out_features
        # TODO 不考虑fold方式，需要计算bias的参数量
        if self.bias is True and self.is_folded is False:
            params += self.out_features
            # print("%d" % self.out_features)
        return params


class Identity_(nn.Module):
    """
    skip connect
    """

    def __init__(self):
        super(Identity_, self).__init__()

    def forward(self, inputs):
        return inputs

def _act(act_type, **kwargs):
    if act_type is None or act_type == "Identity":
        return Identity_()
    elif act_type == "ReLU":
        result = nn.ReLU(inplace=True)
        return result
    else:
        raise Exception("Not implemented !!!")
    

    raise Exception("_act: Go here ..., maybe don\'t define some act")


In [4]:
import math

import numpy as np
import torch
import torch.nn as nn
from torch.nn import init
import torch.nn.functional as F
from einops import rearrange
from einops.layers.torch import Rearrange
from torch.nn.parallel import DataParallel


class TransNetV2Supernet(nn.Module):
    def __init__(self, D=1024,
                 use_many_hot_targets=True,
                 use_frame_similarity=True,
                 use_mean_pooling=None,
                 dropout_rate=0.5,
                 use_resnet_like_top=False,
                 frame_similarity_on_last_layer=False,
                 use_color_histograms=True,
                 chromosome=None):
        super(TransNetV2Supernet, self).__init__()

        self.reprocess_layer = (lambda x: x / 255.)
 
        # TODO Layer 1 - 6
        self.Layer_0_3 = DilatedDCNNV2(3, 16, multiplier=1)
        self.Layer_1_8 = DilatedDCNNV2ABC(16 * 4, 16, multiplier=4, n_dilation=5, st_type="A")
        self.Layer_2_8 = DilatedDCNNV2ABC(16 * 4, 32, multiplier=4, n_dilation=5, st_type="A")
        self.Layer_3_8 = DilatedDCNNV2ABC(32 * 4, 32, multiplier=4, n_dilation=5, st_type="A")
        self.Layer_4_13 = DilatedDCNNV2(32 * 4, 64, multiplier=3, n_dilation=5)
        self.Layer_5_12 = DilatedDCNNV2(64 * 4, 64, multiplier=2, n_dilation=5)
        self.Layer_6_0 = Attention1D(dim_in=256 * 3 * 6, dim_out=1024, num_heads=4,
            qkv_bias=False,
            attn_drop=0.,
            proj_drop=0.,
            with_cls_token=False,
            skip_conv_proj=True,
            n_layer=0
        )

        self.pool = torch.nn.AvgPool3d(kernel_size=(1, 2, 2))

        if use_frame_similarity is True and use_color_histograms is True:
            in_features = 4864
        elif use_frame_similarity is True and use_color_histograms is False:
            in_features = 4736
        elif use_frame_similarity is False and use_color_histograms is True:
            in_features = 4736
        else:
            in_features = 4608

        self.fc1_0 = Linear_(in_features=in_features, out_features=D, bias=True, act="ReLU")
        in_features += 1024
        self.fc1 = Linear_(in_features=in_features, out_features=D, bias=True, act="ReLU")
        self.cls_layer1 = Linear_(in_features=1024, out_features=1, bias=True, act="Identity")
        self.cls_layer2 = Linear_(in_features=1024, out_features=1, bias=True, act="Identity") \
            if use_many_hot_targets else None
        self.frame_sim_layer = FrameSimilarity(in_channels=448, inner_channels=101) if use_frame_similarity else None
        self.color_hist_layer = ColorHistograms(lookup_window=101, output_dim=128) if use_color_histograms else None
        self.use_mean_pooling = use_mean_pooling
        self.dropout = torch.nn.Dropout(p=1.0 - dropout_rate) if dropout_rate is not None else None
        self.frame_similarity_on_last_layer = frame_similarity_on_last_layer
        self.resnet_like_top = use_resnet_like_top
        if self.resnet_like_top:
            raise Exception("Position resnet_like_top 1: should not be here !!!")
        # self.logits_act = torch.nn.Sigmoid()  # TODO put final activation here

        self._init_weights()
        
        

    def _init_weights(self):
        for m in self.modules():
            if isinstance(m, nn.BatchNorm3d):
                m.weight.data.fill_(1)
                m.bias.data.zero_()
            elif isinstance(m, nn.Linear):
                fan_out = m.weight.size(0)
                fan_in = m.weight.size(1)
                limit = math.sqrt(6.0 / (fan_in + fan_out))
                m.weight.data.uniform_(-limit, limit)
                if m.bias is not None:
                    m.bias.data.zero_()
            
            elif isinstance(m, nn.Conv3d):
                init.kaiming_normal_(m.weight, mode="fan_in", nonlinearity="relu")

    def forward(self, inputs, **kwargs):
        x = self.reprocess_layer(inputs)

        if self.resnet_like_top:
            raise Exception("Position resnet_like_top 2: should not be here !!!")

        block_features = []
        shortcut = None
        # TODO Layer 1 ~ 6
        num_layers = 6
        for layer_index in range(num_layers):
            if layer_index == 0:
                op = self.Layer_0_3
            elif layer_index == 1:
                op = self.Layer_1_8
            elif layer_index == 2:
                op = self.Layer_2_8
            elif layer_index == 3:
                op = self.Layer_3_8
            elif layer_index == 4:
                op = self.Layer_4_13
            elif layer_index == 5:
                op = self.Layer_5_12

            x = op(x)
            if layer_index in [0, 2, 4]:
                shortcut = x
            else:
                x = shortcut + x
                x = self.pool(x)
                block_features.append(x)
        transf_x = self.Layer_6_0(x, t=x.size(1), h=3, w=6)

        if self.use_mean_pooling:
            x = torch.mean(x, dim=[3, 4])  # out is [BS, C, N]
        else:
            # TODO actually go here !
            x = x.permute(0, 2, 3, 4, 1)
            shape = [x.shape[0], x.shape[1], np.prod(x.shape[2:])]
            x = x.reshape(shape=shape)  # out is [BS, C, N * H * W]

        if self.frame_sim_layer is not None and not self.frame_similarity_on_last_layer:
            x = torch.cat([self.frame_sim_layer(block_features), x], dim=2)

        if self.color_hist_layer is not None:
            x = torch.cat([self.color_hist_layer(inputs), x], dim=2)
        
        if transf_x is not None:
            x = torch.cat([transf_x, x], dim=2)

            x = self.fc1(x)
        else:
            x = self.fc1_0(x)

        if self.dropout is not None:
            x = self.dropout(x)

        if self.frame_sim_layer is not None and self.frame_similarity_on_last_layer:
            x = torch.cat([self.frame_sim_layer(block_features), x], dim=2)

        one_hot = self.cls_layer1(x)
        # one_hot = self.logits_act(one_hot)

        many_hot = None
        if self.cls_layer2 is not None:
            many_hot = self.cls_layer2(x)
            # many_hot = self.logits_act(self.cls_layer2(x))

        if many_hot != None:
            return one_hot, many_hot
        return one_hot


def gather_nd(params, indices):
    """ The same as tf.gather_nd but batched gather is not supported yet.
    indices is an k-dimensional integer tensor, best thought of as a (k-1)-dimensional tensor of indices into params, where each element defines a slice of params:

    output[\\(i_0, ..., i_{k-2}\\)] = params[indices[\\(i_0, ..., i_{k-2}\\)]]

    Args:
        params (Tensor): "n" dimensions. shape: [x_0, x_1, x_2, ..., x_{n-1}]
        indices (Tensor): "k" dimensions. shape: [y_0,y_2,...,y_{k-2}, m]. m <= n.

    Returns: gathered Tensor.
        shape [y_0,y_2,...y_{k-2}] + params.shape[m:]

    """
    orig_shape = list(indices.shape)
    num_samples = np.prod(orig_shape[:-1])
    m = orig_shape[-1]
    n = len(params.shape)

    if m <= n:
        out_shape = orig_shape[:-1] + list(params.shape)[m:]
    else:
        raise ValueError(f'the last dimension of indices must less or equal to the rank of params. '
                         f'Got indices:{indices.shape}, params:{params.shape}. {m} > {n}')

    indices = indices.reshape((num_samples, m)).transpose(0, 1).tolist()
    output = params[indices]  # (num_samples, ...)
    return output.reshape(out_shape).contiguous()


class FrameSimilarity(nn.Module):

    def __init__(self,
                 in_channels,
                 inner_channels,
                 similarity_dim=128,
                 lookup_window=101,
                 output_dim=128,
                 stop_gradient=False,
                 use_bias=True):
        super(FrameSimilarity, self).__init__()

        self.projection = Linear_(in_features=in_channels, out_features=similarity_dim,
                                  bias=use_bias, act="Identity")
        self.fc = Linear_(in_features=inner_channels, out_features=output_dim, bias=True, act="ReLU")

        self.lookup_window = lookup_window
        self.stop_gradient = stop_gradient
        assert lookup_window % 2 == 1, "`lookup_window` must be odd integer"
        if torch.cuda.is_available() is True:
            self.device = "cuda"
        else:
            self.device = "cpu"

    def forward(self, inputs):
        # pt version [BS, C, N, H, W], so [3, 4] means apply avg on spatial dim, out dim is [BS, C, N]
        x = torch.cat([torch.mean(x, dim=[3, 4]) for x in inputs], dim=1)

        if self.stop_gradient:
            x = x.detach()

        x = x.permute(dims=[0, 2, 1])  # out is [BS, N ,C]
        batch_size, time_window, old_channels = x.shape
        x = x.reshape(shape=[batch_size * time_window, old_channels])  # [BS X N, C]
        x = self.projection(x)
        x = F.normalize(x, p=2, dim=1)  # norm at C dim

        _, new_channels = x.shape
        x = x.reshape(shape=[batch_size, time_window, new_channels])
        y = x.permute(dims=[0, 2, 1])
        similarities = torch.matmul(x, y)  # [batch_size, time_window, time_window]
        # note that it operates on dimensions of the input tensor in a backward fashion (from last dimension to the first dimension)
        similarities_padded = F.pad(similarities,
                                    pad=[(self.lookup_window - 1) // 2, (self.lookup_window - 1) // 2, 0, 0, 0, 0])

        batch_indices = torch.arange(0, batch_size, device=self.device). \
            reshape(shape=[batch_size, 1, 1]). \
            repeat([1, time_window, self.lookup_window])
        time_indices = torch.arange(0, time_window, device=self.device). \
            reshape(shape=[1, time_window, 1]). \
            repeat([batch_size, 1, self.lookup_window])
        lookup_indices = torch.arange(0, self.lookup_window, device=self.device). \
                             reshape(shape=[1, 1, self.lookup_window]). \
                             repeat([batch_size, time_window, 1]) + time_indices

        indices = torch.stack([batch_indices, time_indices, lookup_indices], dim=-1)

        similarities = gather_nd(similarities_padded, indices)
        return self.fc(similarities)

class ColorHistograms(nn.Module):
    
    def __init__(self, lookup_window=101, output_dim=128):
        super(ColorHistograms, self).__init__()
        self.fc = Linear_(in_features=101, out_features=output_dim, bias=True, act="ReLU") \
            if output_dim is not None else None
        self.lookup_window = lookup_window
        assert lookup_window % 2 == 1, "`lookup_window` must be odd integer"
        if torch.cuda.is_available() is True:
            self.device = "cuda"
        else:
            self.device = "cpu"

    def unsorted_segment_sum(self, data, segment_ids, num_segments):
        """
        https://gist.github.com/bbrighttaer/207dc03b178bbd0fef8d1c0c1390d4be
        """
        assert all([i in data.shape for i in segment_ids.shape]), "segment_ids.shape should be a prefix of data.shape"
        # segment_ids is a 1-D tensor repeat it to have the same shape as data
        if len(segment_ids.shape) == 1:
            s = torch.prod(torch.tensor(data.shape[1:])).long()
            segment_ids = segment_ids.repeat_interleave(s).view(segment_ids.shape[0], *data.shape[1:])
        assert data.shape == segment_ids.shape, "data.shape and segment_ids.shape should be equal"
        shape = [num_segments] + list(data.shape[1:])
        tensor = torch.zeros(*shape, device=self.device).scatter_add(0, segment_ids, data.float())
        tensor = tensor.type(data.dtype)
        return tensor

    def compute_color_histograms(self, frames):
        frames = frames.type(dtype=torch.int32)
        # pt version [BS, C, N, H, W]  ---> tf version [BS, N, H, W, C]
        frames = frames.permute(0, 2, 3, 4, 1)

        def get_bin(frames):
            # returns 0 .. 511
            R, G, B = frames[:, :, 0], frames[:, :, 1], frames[:, :, 2]
            R, G, B = R >> 5, G >> 5, B >> 5
            return (R << 6) + (G << 3) + B

        batch_size, time_window, height, width = frames.shape[0], frames.shape[1], frames.shape[2], frames.shape[3]

        no_channels = frames.shape[-1]
        assert no_channels == 3 or no_channels == 6
        if no_channels == 3:
            frames_flatten = frames.reshape(shape=[batch_size * time_window, height * width, 3])
        else:
            frames_flatten = frames.reshape(shape=[batch_size * time_window, height * width * 2, 3])

        binned_values = get_bin(frames_flatten)
        frame_bin_prefix = torch.arange(0, batch_size * time_window, dtype=torch.int32, device=self.device) << 9
        frame_bin_prefix = frame_bin_prefix.unsqueeze(dim=-1)
        binned_values = binned_values + frame_bin_prefix

        ones = torch.ones_like(binned_values, dtype=torch.int32, device=self.device)
        histograms = self.unsorted_segment_sum(data=ones,
                                               segment_ids=binned_values.type(dtype=torch.long),
                                               num_segments=batch_size * time_window * 512)
        histograms = torch.sum(histograms, dim=1)
        histograms = histograms.reshape(shape=[batch_size, time_window, 512])

        histograms_normalized = histograms.type(dtype=torch.float32)
        histograms_normalized = histograms_normalized / torch.norm(histograms_normalized, dim=2, keepdim=True)
        return histograms_normalized

    def forward(self, inputs):
        x = self.compute_color_histograms(inputs)

        batch_size, time_window = x.shape[0], x.shape[1]
        y = x.permute(dims=[0, 2, 1])
        similarities = torch.matmul(x, y)  # [batch_size, time_window, time_window]
        # note that it operates on dimensions of the input tensor in a backward fashion (from last dimension to the first dimension)
        similarities_padded = F.pad(similarities,
                                    pad=[(self.lookup_window - 1) // 2, (self.lookup_window - 1) // 2, 0, 0, 0, 0])

        batch_indices = torch.arange(0, batch_size, device=self.device). \
            reshape(shape=[batch_size, 1, 1]). \
            repeat([1, time_window, self.lookup_window])
        time_indices = torch.arange(0, time_window, device=self.device). \
            reshape(shape=[1, time_window, 1]). \
            repeat([batch_size, 1, self.lookup_window])
        lookup_indices = torch.arange(0, self.lookup_window, device=self.device). \
                             reshape(shape=[1, 1, self.lookup_window]). \
                             repeat([batch_size, time_window, 1]) + time_indices

        indices = torch.stack([batch_indices, time_indices, lookup_indices], dim=-1)

        similarities = gather_nd(similarities_padded, indices)

        if self.fc is not None:
            return self.fc(similarities)
        return similarities


class ConvexCombinationRegularization(nn.Module):

    def __init__(self, ):
        super(ConvexCombinationRegularization, self).__init__()

        raise Exception("ConvexCombinationRegularization: should not init this class !!!")

    def forward(self, inputs):
        pass


class DilatedDCNNV2ABC(nn.Module):
    def __init__(self, in_channels,
                 filters,
                 batch_norm=True,
                 activation=F.relu,
                 octave_conv=False,
                 multiplier=4,
                 n_dilation=4,
                 st_type="A"):
        super(DilatedDCNNV2ABC, self).__init__()
        assert not (octave_conv and batch_norm)

        self.share = torch.nn.Conv3d(in_channels=in_channels,
                                     out_channels=multiplier * filters,
                                     kernel_size=(1, 3, 3),
                                     padding=(0, 1, 1),
                                     dilation=(1, 1, 1),
                                     bias=False)
        init.kaiming_normal_(self.share.weight, mode="fan_in", nonlinearity="relu")

        self.conv_blocks = nn.ModuleList()

        n_in_plane = multiplier * filters
        if st_type == "B":
            n_in_plane = in_channels

        n_filter_per_module = (filters * 4) // n_dilation  # multiplier
        for dilation in range(n_dilation-1):
            self.conv_blocks.append(
                Conv3DConfigurable(
                    n_in_plane,
                    n_filter_per_module,
                    2 ** dilation,
                    mid_filter=n_in_plane,
                    separable=True,
                    sharable=True,
                    use_bias=not batch_norm,
                    octave=octave_conv
                )
            )
        self.conv_blocks.append(
            Conv3DConfigurable(
                n_in_plane,
                (filters * 4) - n_filter_per_module * (n_dilation-1),  # multiplier
                2 ** (n_dilation - 1),
                mid_filter=n_in_plane,
                separable=True,
                sharable=True,
                use_bias=not batch_norm,
                octave=octave_conv
            )
        )

        self.octave = octave_conv
        self.multiplier = multiplier
        self.n_dilation = n_dilation
        self.st_type = st_type

        self.batch_norm = torch.nn.BatchNorm3d(
            num_features=filters * 4,  # multiplier,
            eps=1e-3, momentum=0.1) if batch_norm else None
        self.activation = activation

    def forward(self, inputs):
        feature = self.share(inputs)
        if self.st_type == "A":
            x = []
#             print(len(self.conv_blocks), feature.size())
            for block in self.conv_blocks:
#                 print(block)
                x.append(block(feature))
            x = torch.cat(x, dim=1)
        elif self.st_type == "B":
            x = []
            for block in self.conv_blocks:
                x.append(block(inputs))
            x = torch.cat(x, dim=1)
            x = x + feature
        elif self.st_type == "C":
            x = []
            for block in self.conv_blocks:
                x.append(block(feature))
            x = torch.cat(x, dim=1)
            x = x + feature
        else:
            raise Exception("Not Implemented ST Type" + self.st_type)

        if self.octave:
            raise Exception("Position octave 1: should not be here !!!")

        if self.batch_norm is not None:
            x = self.batch_norm(x)

        if self.activation is not None:
            if self.octave:
                raise Exception("Position octave 2: should not be here !!!")
            else:
                x = self.activation(x)
        return x


class DilatedDCNNV2(nn.Module):
    def __init__(self, in_channels,
                 filters,
                 multiplier=2,
                 n_dilation=4,
                 batch_norm=True,
                 activation=F.relu,
                 octave_conv=False):
        super(DilatedDCNNV2, self).__init__()
        assert not (octave_conv and batch_norm)

        self.n_dilation = n_dilation
        self.conv_blocks = nn.ModuleList()


        n_filter_per_module = (filters * 4) // n_dilation  # multiplier
        for dilation in range(n_dilation-1):
            self.conv_blocks.append(
                Conv3DConfigurable(
                    in_channels,
                    n_filter_per_module,
                    mid_filter=multiplier*filters,
                    dilation_rate=2 ** dilation,
                    use_bias=not batch_norm,
                    octave=octave_conv
                )
            )
        self.conv_blocks.append(
            Conv3DConfigurable(
                in_channels,
                (filters * 4) - n_filter_per_module * (n_dilation-1),  # multiplier
                mid_filter=multiplier*filters,
                dilation_rate=2 ** (n_dilation-1),
                use_bias=not batch_norm,
                octave=octave_conv
            )
        )

        self.batch_norm = torch.nn.BatchNorm3d(num_features=filters * 4, eps=1e-3, momentum=0.1) if batch_norm else None
        self.activation = activation
        self.octave = octave_conv

    def forward(self, inputs):
        x = []
        for block in self.conv_blocks:
            x.append(block(inputs))
        x = torch.cat(x, dim=1)

        if self.octave:
            raise Exception("Position octave 1: should not be here !!!")


        if self.batch_norm is not None:
            x = self.batch_norm(x)

        if self.activation is not None:
            if self.octave:
                raise Exception("Position octave 2: should not be here !!!")
            else:
                x = self.activation(x)
        return x


class Conv3DConfigurable(nn.Module):
    def __init__(self, in_channels,
                 filters,
                 dilation_rate,
                 mid_filter=None,
                 separable=True,
                 sharable=False,
                 octave=False,
                 use_bias=False):
        super(Conv3DConfigurable, self).__init__()
        assert not (separable and octave)

        if separable:
            # (2+1)D convolution https://arxiv.org/pdf/1711.11248.pdf
            from torch.nn import init
            self.layers = nn.ModuleList()
            if not sharable:
                conv1 = torch.nn.Conv3d(in_channels=in_channels,
                                        out_channels=2 * filters if mid_filter is None else mid_filter,
                                        kernel_size=(1, 3, 3),
                                        padding=(0, 1, 1),
                                        dilation=(1, 1, 1),
                                        bias=False)
                init.kaiming_normal_(conv1.weight, mode="fan_in", nonlinearity="relu")
                self.layers.append(conv1)

            conv2 = torch.nn.Conv3d(in_channels=2 * filters if mid_filter is None else mid_filter,
                                    out_channels=filters,
                                    kernel_size=(3, 1, 1),
                                    padding=(1 * dilation_rate, 0, 0),
                                    dilation=(dilation_rate, 1, 1),
                                    bias=use_bias)
            init.kaiming_normal_(conv2.weight, mode="fan_in", nonlinearity="relu")
            self.layers.append(conv2)
        elif octave:
            raise Exception("Positon octave 3: should not be here !!!")
        else:
            raise Exception("Positon else 1: should not be here !!!")

    def forward(self, inputs):
        x = inputs
        for layer in self.layers:
            x = layer(x)
        return x
    
    
class Attention1D(nn.Module):
    def __init__(self,
                 dim_in,
                 dim_out,
                 num_heads,
                 qkv_bias=False,
                 attn_drop=0.,
                 proj_drop=0.,
                 with_cls_token=False,
                 skip_conv_proj=False,
                 n_layer=1,
                 **kwargs
                 ):
        super().__init__()
        self.dim = dim_out
        self.num_heads = num_heads
        self.n_layer = n_layer
        # head_dim = self.qkv_dim // num_heads
        self.scale = dim_out ** -0.5
        self.with_cls_token = with_cls_token
        
        self.proj_q = nn.ModuleList()
        self.proj_k = nn.ModuleList()
        self.proj_v = nn.ModuleList()
        self.attn_drop = nn.ModuleList()
        self.proj = nn.ModuleList()
        self.proj_drop = nn.ModuleList()
        
        for _ in range(n_layer):
            self.proj_q.append(nn.Linear(dim_in, dim_out, bias=qkv_bias))
            self.proj_k.append(nn.Linear(dim_in, dim_out, bias=qkv_bias))
            self.proj_v.append(nn.Linear(dim_in, dim_out, bias=qkv_bias))

            self.attn_drop.append(nn.Dropout(attn_drop))
            self.proj.append(nn.Linear(dim_out, dim_out))
            self.proj_drop.append(nn.Dropout(proj_drop))
            
            dim_in = dim_out

    def forward(self, x, t, h, w):
        x = rearrange(x, 'b c t H W -> b t (c H W)')
        if self.n_layer == 0:
            return None
        
        for idx in range(self.n_layer):
            q = rearrange(self.proj_q[idx](x), 'b t (h d) -> b h t d', h=self.num_heads)
            k = rearrange(self.proj_k[idx](x), 'b t (h d) -> b h t d', h=self.num_heads)
            v = rearrange(self.proj_v[idx](x), 'b t (h d) -> b h t d', h=self.num_heads)

            attn_score = torch.einsum('bhlk,bhtk->bhlt', [q, k]) * self.scale
            attn = F.softmax(attn_score, dim=-1)
            attn = self.attn_drop[idx](attn)

            x = torch.einsum('bhlt,bhtv->bhlv', [attn, v])
            x = rearrange(x, 'b h t d -> b t (h d)')

            x = self.proj[idx](x)
            x = self.proj_drop[idx](x)
        return x

In [5]:
import os
import torch
import numpy as np
from typing import List, Optional
from tqdm.notebook import tqdm

In [6]:
class AutoShot:
    """
    A class for automatic shot detection in video using the TransNetV2Supernet model.

    This class provides functionality to detect scene changes (shots) in a video
    using a pre-trained neural network model. It's particularly useful in video
    analysis tasks such as content summarization, scene indexing, or video editing.

    Attributes:
        device (str): The device on which the model will run ('cpu' or 'cuda').
        model (torch.nn.Module): The loaded TransNetV2Supernet model.

    Example:
        >>> shot_detector = AutoShot("path/to/pretrained/model.pth")
        >>> scenes = shot_detector.process_video("path/to/video.mp4")
        >>> print(f"Detected {len(scenes)} scenes in the video.")
    """

    def __init__(
        self,
        pretrained_path: str,
        device: Optional[str] = None
    ):
        """
        Initialize the AutoShot class.

        Args:
            pretrained_path (str): Path to the pretrained model weights file.
            device (Optional[str]): Device to run the model on ('cpu' or 'cuda').
                If None, it will use CUDA if available, else CPU.

        Raises:
            RuntimeError: If the model fails to load.
        """
        self.device = device or ('cuda' if torch.cuda.is_available() else 'cpu')
        self.model = self.load_model(pretrained_path=pretrained_path)
        
    
    def load_model(self, pretrained_path: str) -> torch.nn.Module:
        """
        Loading the pretrained model

        Args:
            pretrained_path (str): Path to the pretrained model weights

        Raises:
            FileNotFoundError: The pretrained file is missing
            RuntimeError: If loading model process is not successful

        Returns:
            torch.nn.Module : loaded and configured model
        """
        try:
            model =  TransNetV2Supernet().eval()
            if not os.path.exists(pretrained_path):
                raise FileNotFoundError(f"Can't find the pretrained model path at {pretrained_path}")
            
            print(f"Loading the pretrained model from {pretrained_path}")
            model_dict = model.state_dict()
            pretrained_dict = torch.load(pretrained_path, map_location=self.device, weights_only=True)
            pretrained_dict = {k: v for k, v in pretrained_dict['net'].items() if k in model_dict}
            print(f"Current model has {len(model_dict)} params, Updating {len(pretrained_dict)} params")
            model_dict.update(pretrained_dict)
            model.load_state_dict(model_dict)
            return model.to(self.device)
        except Exception as e:
            raise RuntimeError(f"Failed to load the model. Did you piss off the AI gods? Error: {str(e)}")
    
    def predict(self, batch: np.ndarray) -> np.ndarray:
        """Make predictions on the batch of frames

        Args:
            batch (np.ndarray): Batch of video frames, in the shape of (height, width, color_channel, frames)
            typically: (27, 48, channels=3, frames = 100)

        Returns:
            np.ndarray: Predictions of the batch
        """
        with torch.no_grad():
            batch = torch.from_numpy(batch.transpose((3, 0, 1, 2))[np.newaxis, ...]) * 1.0
            batch = batch.to(self.device)
            one_hot = self.model(batch)

            if isinstance(one_hot, tuple):
                one_hot = one_hot[0]
            return torch.sigmoid(one_hot[0]).cpu().numpy()
    
    def detect_shots(self, frames: np.ndarray) -> np.ndarray:
        """Detects shot in a video

        Args:
            frames (np.ndarray): Array of video frames, (num_frames, height, width, channels)

        Returns:
            np.ndarray: shot detection predictions for each frame
        """
        predictions= []
        
        for batch in tqdm(get_batches(frames=frames), desc="Dectecting shots", unit="batch"):
            prediction = self.predict(batch=batch)
            predictions.append(prediction[25:75])
        
        return np.concatenate(predictions, axis=0)[:len(frames)]
    
    @staticmethod 
    def predictions_to_scenes(predictions: np.ndarray, threshold: float = 0.5) -> np.ndarray:
        """
        Convert frame-wise predictions to scene boundaries.

        Args:
            predictions (np.ndarray): Array of frame-wise predictions
            threshold (float, optional): Threshold for considering a frame as a shot boundary. Defaults to 0.5

        Returns:
            np.ndarray: List of scene start and end frame indices
        """
        predictions = (predictions > threshold).astype(np.uint8)
        scenes = []
        t, t_prev, start = -1, 0, 0
        for i, t in enumerate(predictions):
            if t_prev == 1 and t == 0:
                start = i
            if t_prev == 0 and t == 1 and i != 0:
                scenes.append([start, i])
            t_prev = t
        if t == 0:
            scenes.append([start, i])

        # just fix if all predictions are 1
        if len(scenes) == 0:
            return np.array([[0, len(predictions) - 1]], dtype=np.int32)
        return np.array(scenes, dtype=np.int32)

    def process_video(self, video_path: str) -> List[List[int]]:
        try:
            if not os.path.exists(video_path):
                raise FileNotFoundError(f"File not found: {video_path}")

            frames = get_frames(video_file_path=video_path)
            if frames is None or len(frames) == 0:
                raise ValueError(f"No frames extracted from video: {video_path}")
            
            predictions = self.detect_shots(frames = frames)
            scenes = self.predictions_to_scenes(predictions=predictions)

            return scenes.tolist()

        except Exception as e:
            raise RuntimeError(F"Failed to process video: {video_path}. Error: {e}")


In [7]:
import numpy as np
import ffmpeg

def get_frames(video_file_path: str, width: int = 48, height: int = 27) -> np.ndarray:
    """
    Extract frames from video 
    Args:
        video_file_path (str): Path to the video file.
        width (int): Width of the extracted frame. Default is 48
        height (int): Height of the extracted frames. Default is 27
    Returns:
        np.ndarray: Array of video frames
    """
    try:
        out, _ = (
             ffmpeg
            .input(video_file_path)
            .output('pipe:', format='rawvideo', pix_fmt='rgb24', s=f'{width}x{height}')
            .run(capture_stdout=True, capture_stderr=True)
        )
        video = np.frombuffer(out, np.uint8).reshape([-1, height, width, 3])
        return video
    except ffmpeg.Error as e:
        print(f"ffmpeg error: {e.stderr.decode()}")
        raise
    except Exception as e:
        print(f"Error in get_frames: {str(e)}")
        raise

def get_batches(frames: np.ndarray):
    """
    Prepare batches of frames for processing. It's like making a video sandwich.
    
    Args:
        frames (np.ndarray): Array of video frames. Try not to feed it pictures of your ex.
    
    Yields:
        np.ndarray: Batches of frames, because processing all at once would make your computer cry.
    """
    reminder = 50 - len(frames) % 50
    if reminder == 50:
        reminder = 0
    frames = np.concatenate([frames[:1]] * 25 + [frames] + [frames[-1:]] * (reminder + 25), 0)

    
    for i in range(0, len(frames) - 50, 50):
        yield frames[i:i + 100]

In [8]:
import os
import logging
from typing import Dict, Any

def process_single_video(video_path: str, shot_detector: AutoShot) -> Dict[str, Any]:
    """
    Process a single video file to detect shots.

    Args:
        video_path (str): Path to the video file.
        shot_detector (AutoShot): Instance of AutoShot for scene detection.

    Returns:
        Dict[str, Any]: A dictionary containing processing results.
    """
    result = {"video_path": video_path, "status": "success", "scenes": None}
    
    try:
        scenes = shot_detector.process_video(video_path=video_path)
        result["scenes"] = scenes
        
        if not scenes:
            logging.warning(f"No scenes detected in video: {video_path}")
    except Exception as e:
        logging.error(f"Error processing video {video_path}: {str(e)}")
        result["status"] = "error"
        result["error_message"] = str(e)
    
    return result

In [9]:
import os
from typing import Dict, Any, Iterator, List
from tqdm.notebook import tqdm
import logging
import threading
import json
import time
import numpy as np

In [10]:
VIDEO_EXTENSIONS = ('.mp4', '.avi', '.mov', '.mkv')

def ensure_json_output_path(source_root: str, output_root: str, video_path: str) -> str:
    rel_path = os.path.relpath(video_path, source_root)
    json_rel_path = os.path.splitext(rel_path)[0] + ".json"
    destination = os.path.join(output_root, json_rel_path)
    os.makedirs(os.path.dirname(destination), exist_ok=True)
    return destination

def write_scene_json(output_path: str, result: Dict[str, Any], video_path: str) -> None:
    payload = {
        "video_path": video_path,
        "status": result.get("status", "error"),
        "scenes": result.get("scenes", [])
    }
    if "error_message" in result:
        payload["error_message"] = result["error_message"]
    with open(output_path, 'w', encoding='utf-8') as f:
        json.dump(payload, f, indent=2, ensure_ascii=False)

def dfs_get_video_paths(input_dir: str) -> Iterator[str]:
    """
    Perform an iterative depth-first search to find video files.

    Args:
        input_dir (str): The root directory to search for videos.

    Yields:
        str: Paths to video files.
    """
    stack = [input_dir]

    while stack:
        current_dir = stack.pop()
        with os.scandir(current_dir) as entries:
            for entry in entries:
                if entry.is_dir():
                    stack.append(entry.path)
                elif entry.is_file() and entry.name.lower().endswith(VIDEO_EXTENSIONS):
                    yield entry.path

def get_video_folders(root_dir: str) -> List[str]:
    """
    Get all immediate subdirectories containing video files.
    
    Args:
        root_dir (str): Root directory to search.
    
    Returns:
        List[str]: List of folder paths containing videos.
    """
    folders = []

    with os.scandir(root_dir) as entries:
        for entry in entries:
            if entry.is_dir():
                has_videos = False
                with os.scandir(entry.path) as sub_entries:
                    for sub_entry in sub_entries:
                        if sub_entry.is_file() and sub_entry.name.lower().endswith(VIDEO_EXTENSIONS):
                            has_videos = True
                            break
                if has_videos:
                    folders.append(entry.path)

    return sorted(folders)

def process_videos(input_root: str, pretrained_model_path: str, output_root: str) -> Dict[str, Dict[str, Any]]:
    shot_detector = AutoShot(pretrained_model_path)
    video_paths = list(dfs_get_video_paths(input_root))
    results: Dict[str, Dict[str, Any]] = {}
    logging.info(f"Processing {len(video_paths)} videos under {input_root}")
    for video_path in tqdm(video_paths, desc=f"Processing {os.path.basename(input_root)}", unit="video"):
        output_path = ensure_json_output_path(input_root, output_root, video_path)
        result = process_single_video(video_path, shot_detector)
        write_scene_json(output_path, result, video_path)
        results[os.path.relpath(video_path, input_root)] = result
    return results

def process_folder(folder_path: str, pretrained_model_path: str, output_dir: str) -> Dict[str, Dict[str, Any]]:
    return process_videos(folder_path, pretrained_model_path, output_dir)

In [11]:
class KaggleSessionKeeper(threading.Thread):
    def __init__(self, delay_min=175, delay_max=185):
        super(KaggleSessionKeeper, self).__init__()
        self.delay_min = delay_min
        self.delay_max = delay_max
        self.running = False
        self.program_running = True
        self.action_count = 0

    def start_actions(self):
        self.running = True

    def stop_actions(self):
        self.running = False

    def exit(self):
        self.stop_actions()
        self.program_running = False

    def run(self):
        while self.program_running:
            while self.running:
               
                print("Keeping session active...")
                self.action_count += 1
                print(f"Action {self.action_count} performed")
                
                delay = np.random.uniform(self.delay_min, self.delay_max)
                time.sleep(delay)
            time.sleep(0.1)
def main_process():
    input_dirs = [
        '/kaggle/input/irbatch2/IRbatch2/L13',
        '/kaggle/input/irbatch2/IRbatch2/L14',
        '/kaggle/input/irbatch2/IRbatch2/L15',
        '/kaggle/input/irbatch2/IRbatch2/L16',
        '/kaggle/input/irbatch2/IRbatch2/L17',
        '/kaggle/input/irbatch2/IRbatch2/L18',
        '/kaggle/input/irbatch2/IRbatch2/L19',
        '/kaggle/input/irbatch2/IRbatch2/L20',
        '/kaggle/input/irbatch2/IRbatch2/L21',
        '/kaggle/input/irbatch2/IRbatch2/L22',
        '/kaggle/input/irbatch2/IRbatch2/L23',
        '/kaggle/input/irbatch2/IRbatch2/L24',

    ]
    pretrained_model_path = "/kaggle/input/model-weights-autoshot/ckpt_0_200_0.pth"
    output_root = "/kaggle/working"

    for input_dir in input_dirs:
        output_dir = os.path.join(output_root, os.path.basename(input_dir))
        os.makedirs(output_dir, exist_ok=True)
        process_videos(input_dir, pretrained_model_path, output_dir)

session_keeper = KaggleSessionKeeper()
session_keeper.start()
session_keeper.start_actions()

main_process()

session_keeper.exit()
session_keeper.join()

print("All processes completed.")

Keeping session active...
Action 1 performed
Loading the pretrained model from /kaggle/input/model-weights-autoshot/ckpt_0_200_0.pth
Current model has 90 params, Updating 90 params


Processing L13:   0%|          | 0/30 [00:00<?, ?video/s]

Dectecting shots: 0batch [00:00, ?batch/s]

Dectecting shots: 0batch [00:00, ?batch/s]

Keeping session active...
Action 2 performed


...

Dectecting shots: 0batch [00:00, ?batch/s]

Keeping session active...
Action 136 performed


Dectecting shots: 0batch [00:00, ?batch/s]

Dectecting shots: 0batch [00:00, ?batch/s]

All processes completed.
